### Examples of usage of PyWIT

In [19]:
from PyM import *

#### Power functions

#### `s2n` and `n2s`

For the elementary symmetric polynomials (s) and the Newton sums (n)
of the variables $[x_1,x_2,\dotsc]$, `s2n` expresses the $n$'s in
terms of the $s$'s and `n2s` goes the other way around.
See Fulton's *Intersection Theory*, p.56. 

In [2]:
def s2n(s, r=''):
    if r == '': r = len(s)
    if s==[] or r==0: return []
    n = [s[0]]
    if r==1: return n
    x = [t for t in s]
    x = pad(witdual(x),r)
    for k in range(1,r):
        nk = -(convolution(x,n,k-1) + (k+1)*x[k])
        n += [nk]
    return vector(n)

def n2s(n,r=''):
    if r == '' or r>len(n): r = len(n)
    if n==[] or r==0: return []
    y = [t for t in n]
    s = [-y[0]]
    if r==1: return witdual(s)
    for k in range(1,r):
        sk = -(convolution(s,y,k-1) + y[k])/(k+1)
        s += [sk]
    return vector(witdual(s))

[P,x1,x2,x3] = polynomial_ring(Z_,'x',3)
x = [x1,x2,x3]
s= [s1,s2,s3]=[x1+x2+x3,x1*x2+x1*x3+x2*x3,x1*x2*x3]
n = s2n(s)
show('n =',n)
s = n2s(n,3)
show('s =',s)

n = [x1 + x2 + x3, x1**2 + x2**2 + x3**2, x1**3 + x2**3 + x3**3] 

s = [x1 + x2 + x3, x1*x2 + (x1 + x2)*x3, x1*x2*x3] 



#### `c2p` and `p2c`

If $c=[c_1,c_2,...]$ and $[n_1,n_2,...]$ are the elementary
symmetric polynomials and the Newton sums of the
variables $[x_1,x_2,...]$, `c2p` maps $c$ to $p=[n_1/1!,n_2/2!,...]$
and `p2c` goes the other way around.

In [3]:
def c2p(c,r=''):
    n = s2n(c,r)
    if isinstance(n,list):
        n = vector(n)
    if K_(n) == ZZ():
        return vector([QQ_type(Q_,n[k],factorial(k+1)) for k in range(len(n))])
    return vector([n[k]/factorial(k+1) for k in range(len(n))])

def p2c(p,r=''):
    #if isinstance(p,Vector_type): return vector(p2c(list(p),r))
    return n2s([factorial(k+1)*p[k] for k in range(len(p))],r)


p = c2p(s,4)
show('p =',p)
c = p2c(p)
show('c =',c)

p = [x1 + x2 + x3, 1/2*x1**2 + 1/2*x2**2 + (1/2)*x3**2, 1/6*x1**3 + 1/6*x2**3 + (1/6)*x3**3, 1/24*x1**4 + 1/24*x2**4 + (1/24)*x3**4] 

c = [x1 + x2 + x3, x1*x2 + (x1 + x2)*x3, x1*x2*x3, 0] 



#### Sheaves and varieties

Varieties and sheaves are represented by instances of the classes `VAR` and `SHEAF`. 

Roughly speaking, a class is a record scheme that represents some sort of objects. Specific objects of the class are represented by instances of that scheme. The slots in the scheme may hold convenient data or funtions that encode computations which can be performed on any instance. 

For example, a variety `X` (a `VAR` record), has a dimension field `_dim`, and its value is provided by the expression `X._dim`, or also `X.dim()`. The more familiar expression `dim(X)` yields the same value, as `dim(X)` is defined as the (external) function that returns `X._dim`.

Similarly, a sheaf `F` (a `SHEAF` record) has a field `_rank` that holds its rank, and this 
value can be elicited by any one of the expressions `F._rank`, `F.rank()`, or `rank(F)`.

To get instances of a class we need *constructor* functions. In the case of `VAR`, the generic
constructor is `variety`. Its first parameter, mandatory, is the dimension. Optionally, 
we can provided a table as a second parameter specifying the values we want to 
give to various fields of its record. In the case of `SHEAF`, the name of the generic constructor is`SH` and has two mandatory parameters: the rank, in the first place, and
and its chern character, represented as a vector, in the second place. The variety on which
the sheaf is defined can be specified as a third optional parameter. 

Since sheaves are usually specified by providing its chern classes, we can conveniently
resort to the constructor `sheaf`. It has two mandatory parameters. The first is to specify
the rank, as in `SH`, and the second to specify the list (or vector) of chern classes. 
In case we need to use as chern classes symbols `c1,...,cr`, where `c` stands for a stem symbol (string), the constructor of choice is `bundle(r,'c')`, with optional parameters as in the case
of `sheaf`.

In [4]:
#Sheaves
[P,c1,c2,c3] = polynomial_ring(Z_,'c',3)
F = sheaf(2,[c1,c2])
show('F =',F)
B = bundle(3,'s')
show('B =',B)
T = trivial_bundle(3)
show('T =',T)
c = chern_vector(B)
show('c =',c)

F = SH(2, [c1, 1/2*c1**2 - c2]) 

B = SH(3, [s1, 1/2*s1**2 - s2, 1/6*s1**3 -1/2*s1*s2 + (1/2)*s3]) 

T = SH(3, [0, 0, 0]) 

c = [s1, s2, s3] 



In [16]:
X = variety(7)
show('X:',X)
T = {'gcs':vector([c1,c2]), 'monomial_values':{c1**3*c2**2:1, c1**2*c2**3:1}}
Y=variety(5, T)
show('Y:',Y)

X: Variety of dimension 7 

Y: Variety of dimension 5, gcs = [c1, c2], monomials values = {c1**2*c2**3: 1, c1**3*c2**2: 1} 



#### Algebraic curve

In [6]:
def algebraic_curve(g, P):
    [_,P] = polynomial_ring(Q_,P)
    n = 1
    T = {   'kind': 'algebraic_curve',
        'gcs': vector([P]),
        'degs': vector([1]),
        'relations': [P*P],
        'pt': P,
        'monomial_values': {P: 1},
        'tan_bundle': SH(1,vector([collect((2-2*g)*P,P)])),
        'todd_class': vector([collect((1-g)*P,P)])
    }
    return variety(n,T)

C= algebraic_curve(3,'P')
show('C:',C)

C: Variety of dimension 1, gcs = [P], kind = algebraic_curve, degs = [1], monomials values = {P: 1}, pt = P, relations = [P**2], tan budle = SH(1, [-4*P]), todd class = [-2*P] 



#### Projective spaces

In [18]:
def projective_space(n, h):
    [_,h] = polynomial_ring(Q_,h)
    S = sheaf(n,vector([binom(n+1,j)*h**j for j in range(1,n+1)]),n)
    if n == 1:
        kd = 'projective_line'
    elif n == 2:
        kd = 'projective_plane'
    else:
        kd = 'projective_space of dimension ' + n.__str__()    
    T = {
        'kind': kd,
        'gcs': vector([h]),
        'degs': vector([1]),
        'relations': [h**(n+1)],
        'monomials': [[h**j] for j in range(1,n+1)],
        'monomial_values': {h**n : 1},
        'pt': h**n,
        'tan_bundle': S,
        'todd_class': S.todd_vector(n)
    }
    return [variety(n,T), h]

P2,h=projective_space(2,'h')
P3,H = projective_space(3,'H')
show('pt(P2) =', pt(P2))
show('pt(P3) =', pt(P3))
show('Todd Class =',todd_class(P3))
show('Tangent Bundle:', tan_bundle(P3))

pt(P2) = h**2 

pt(P3) = H**3 

Todd Class = [2*H, (11/6)*H**2, H**3] 

Tangent Bundle: SH(3, [4*H, 2*H**2, (2/3)*H**3]) 



### Grassmannians 

In [8]:
def grassmannian(k, n, c = 'c'):
    dim = (k+1)*(n-k)
    S = bundle(k+1, c, dim)
    T = trivial_bundle(n+1,dim)
    Q = T/S.dual()
    C = S.chern_vector()
    M = [monomial_list(C,range(1,k+2),j) for j in range(1,dim+1)]
    R = take(invert_vector(C,n+1),-k-1) 
    
    pt = C[k]**(n-k)
    d = {
        'kind': 'grassmannian', 
        'tautological_bundle': S,
        'tautological_quotient': Q,
        'gcs': C,
        'degs': vector([l for l in range(1,k+2)]),
        'relations': R,
        'pt': pt,
        'monomials': M,
        'monomial_values':find_monomial_values((k+1)*(n-k),C,list(range(1,k+2)),R,pt),
        'tan_bundle': Q.hom(S.dual()),
        'todd_class': Q.hom(S.dual()).todd_vector()
    }
    return [variety(dim,d)]+list(C[:])

#### Lines meeting 4 lines in $\mathbf{P}^3$

In [9]:
k = 1
n = 3
d = (k+1)*(n-1)
G,s1,s2 = grassmannian(k,n,'s')
show('gcs(G) =', gcs(G))
N = integral(G,s1**d)
show('N =', N)

gcs(G) = [s1, s2] 

N = 2 



#### Lines meeting 6 planes in $\mathbf{P}^4$

In [10]:
k = 1
n = 4
d = (k+1)*(n-k)
G,s1,s2 = grassmannian(k,n,'s')
N = integral(G,s1**d)
show('N =',N)

N = 5 



#### Lines contained in a cubic in $\mathbf{P}^3$

In [11]:
k = 1
n = 3
G,c1,c2 =  grassmannian(k,n,'c')
S=tautological_bundle(G)
SD = S.dual()
show('cS =',chern_vector(S))
show('cS* =',chern_vector(SD))
F=symm(3,SD)
show('cF =', chern_vector(F))
c4=chern(F,rank(F))
show('c4F =',c4)
N=integral(G,c4) 
show('N =',N)

cS = [c1, c2] 

cS* = [-c1, c2] 

cF = [-6*c1, 11*c1**2 + 10*c2, -6*c1**3 - 30*c1*c2, 18*c1**2*c2 + 9*c2**2] 

c4F = 18*c1**2*c2 + 9*c2**2 

N = 27 



#### Lines contained in a quintec in $\mathbf{P}^4$

In [12]:
k = 1
n = 4
G,c1,c2 = grassmannian(k,n,'c')
show('dim(G) =',dim(G))
S = tautological_bundle(G)
F = symm(5,S.dual())
c6 = chern(F,rank(F))
show('c6 =',c6)
N = integral(G,c6)
show('N =',N)

dim(G) = 6 

c6 = 600*c1**4*c2 + 1450*c1**2*c2**2 + 225*c2**3 

N = 2875 



#### Conics meeting 8 lines in $\mathbf{P}^3$

In [13]:
G,c1,c2,c3 = grassmannian(2,3,'c')
show('dim(G) =', dim(G))
S = tautological_bundle(G)
E = symm(2,S)
show('E =', E)

P,p = projective_bundle(G,E,'p')
show('dim(P) =', dim(P))
c = 2*c1+p
c = lowerstar(P,c**8)
N = integral(G,c)
show(N)

dim(G) = 3 

E = SH(6, [4*c1, 3*c1**2 - 5*c2, 5/3*c1**3 -9/2*c1*c2 + (7/2)*c3]) 

dim(P) = 8 

92 



#### Conics tangent to 5 conics in $\mathbf{P}^3$

In [14]:
P5,H = projective_space(5,'H')
S,h = projective_space(2,'h')
i = morphism(S,P5,[2*h])
X,D = blowup(i,'D')
show('Monomial_values =', monomial_values(X))
C = (6*H-2*D)**5
show('C =', C)
N = integral(X,C)
show('N =', N)

Monomial_values = {D*H**4: 0, D**4*H: 18, D**2*H**3: 0, D**5: 51, D**3*H**2: 4, H**5: 1} 

C = -32*D**5 + 480*D**4*H - 2880*D**3*H**2 + 8640*D**2*H**3 - 12960*D*H**4 + 7776*H**5 

N = 3264 



#### Conics contained in a quintic in $\mathbf{P}^4$

In [15]:
G,c1,c2,c3 = grassmannian(2,4,'c')
S = tautological_bundle(G)
Q = symm(2,S.dual())
P,z = projective_bundle(G,Q,'z')
S5 = symm(5,S.dual())
S3 = symm(3,S.dual())
F = S5/(S3 * o_(-z,P.dim()))
C = chern(F,rank(F))
c = lowerstar(P,C)
N = integral(G,c)
show('N =',N)

N = 609250 

